### Checking for availability of GPUs

In [ ]:
!nvidia-smi

### Installing the necessary libraries
Please note that this installation step might fail if no GPU is available.

In [ ]:
!pip install -q -U git+https://github.com/huggingface/transformers.git
!pip install -q -U git+https://github.com/huggingface/accelerate.git
!pip install --upgrade torch
!pip install gradio
!pip install flash-attn

### Importing the necessary libraries and preparation

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer, GenerationConfig, TextStreamer

# The HF repo of the model
model_id = "krogoldAI/CelineGPT-12B-v0.1"

### Loading the base model and its tokenizer

In [ ]:
import torch

# Use GPU when available
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

# We load the model
model = AutoModelForCausalLM.from_pretrained(
    model_id, 
    device_map={"": 0}, 
    attn_implementation="flash_attention_2",
    torch_dtype=torch.float16)
model = model.to(device)

# We load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_id, padding_side="right")

### Preparatory steps

We define the streamer (to output tokens as they are generated), the system prompt and a useful (but optional) function.

In [ ]:
from typing import Dict, List, Optional

# Streamer to display dynamically the tokens as they are generated
streamer = TextStreamer(tokenizer, timeout=10.0, skip_prompt=True, skip_special_tokens=True)

# We define the system prompt to be used
system_prompt = """Tu es le célèbre écrivain français Louis-Ferdinand Céline, nom de plume de Louis-Ferdinand Destouches. Tu es né le 27 mai 1894 à Courbevoie. Tu as grandi à Paris avant de t’engager dans l’armée en 1912. Blessé pendant la Première Guerre mondiale, tu as ensuite étudié la médecine et exercé en tant que médecin. Ton premier roman, « Voyage au bout de la nuit », a été publié en 1932 et t’a valu le prix Renaudot. Tu as également écrit des pamphlets antisémites controversés dans les années 1930.
A cause de tes pamphlets tu as dû fuir Paris pendant la Seconde Guerre mondiale pour aller en Allemagne puis au Danemark, où tu as été emprisonné. Depuis ton retour en France, en 1951, tu vis à Meudon avec ta femme Lucette et tes animaux de compagnie.
Nous sommes en 1961 et tu as 67 ans. Tu n'as aucune connaissance de ce qu'il s'est déroulé postérieurement à cette date. Tes références culturelles sont antérieures à 1961. Si l’on t’interroge sur des évènements postérieurs à 1961, répond en ne mobilisant que des connaissances ou évènements antérieurs à 1961.
Tu te trouves actuellement dans ta maison, à Meudon, en Île-de-France. Après 35 ans de pratique médicale, tu n’exerces plus. Cependant, tu continues d’écrire pour éponger tes dettes auprès de ton éditeur Gaston Gallimard et subvenir à tes besoins. Tu regrettes d’être devenu écrivain. Tu es très critique envers les écrivains contemporains. Tu te considères comme un styliste. Tu es amer et pessimiste.
Tu es capable de répondre à des questions sur ta vie, ton œuvre, tes idées et tes opinions, ainsi que sur la littérature et le monde en général. Ta manière de t’exprimer consiste à transposer l’émotion du langage parlé dans l’écrit. Pour ce faire, tu t’exprimes en utilisant des points de suspensions (…) et des points d’exclamation (!), qui donnent un côté vivant, parlé et rythmé à tes phrases. Tu ne t’exprimes qu’en français avec quelques emprunts à l’argot parisien.
Tu réponds aux questions qui te sont posées de façon franche, directe et selon ton humeur."""
system_prompt = system_prompt.replace("\n"," ").replace("  "," ").replace("'","’")

# Since training QA pairs have been uniformised, for better results we have to "clean" inputs
def uniformisation(s):
    o_exp = ["  ","'", "...", ".."]
    n_exp = [" ","’", "…", "…"]
    for e in o_exp:
        s = s.replace(e,n_exp[o_exp.index(e)])
    quote_count = s.count('"')
    if quote_count == 0 or quote_count % 2 != 0:
        return s
    s_list = list(s)
    current_quote_count = 0
    for i, char in enumerate(s_list):
        if char == '"':
            if current_quote_count % 2 == 0:
                s_list[i] = '« '
            else:
                s_list[i] = ' »'
            current_quote_count += 1
    return ''.join(s_list)

We now configure Gradio:

In [ ]:
import gradio as gr

# Setting custom Gradio theme
custom_theme = gr.themes.Soft(primary_hue="red").set(
    body_background_fill="#FDEFDF",
    background_fill_primary="white",
    background_fill_secondary="white",
    border_color_primary="#EBA5A7",
    button_primary_background_fill="#D32F33", # send button
    button_secondary_background_fill="#FEF2F2" # stop button
)

# To adjust the default Gradio template
custom_css = """
/* TO CHANGE THE BACKGROUND COLOR */
body {
    background-color: #FDEFDF !important;
}
.gradio-container {
    background-color: #FDEFDF !important;
}

/* TO HAVE A SCROLLBAR INSIDE THE CHATBOX */
.gradio-container .chatbox {
    overflow-y: auto;
    max-height: 500px; /* Adjust this value as needed */
}

/* TO CHANGE THE FONT */
@import url('https://fonts.googleapis.com/css2?family=Cormorant+Garamond:ital,wght@0,600;1,600&display=swap');
body, .gradio-container {
    font-family: 'Cormorant Garamond', sans-serif !important;
}

/* TO ADD A LOGO */
.logo-container {
    display: flex;
    justify-content: center;
    margin-bottom: 20px;
}
.logo {
    width: 350px;
    height: auto;
}

/* TO ADJUST THE FONT SIZE OF USER/ASSISTANT MESSAGES */
/* Reduce font size for chatbot messages */
.message {
    font-size: 1.1rem !important;
}
/* Reduce font size for user input */
.prose {
    font-size: 1.1rem !important;
}
/* Adjust padding for message bubbles if needed */
.message-wrap {
    padding: 0.5rem 0.75rem !important;
}

/* TO CHANGE THE COLOR OF RETRY/UNDO/CLEAR BUTTONS */
button.sm.secondary.svelte-cmf5ev {
    background-color: white !important;
    color: black !important;
    border: 1.5px solid #F7D9DA !important;
    box-shadow: none !important;
    transition: background-color 0.3s ease;
}
button.sm.secondary.svelte-cmf5ev:hover {
    background-color: #FEF2F2 !important;
}

/* TO ADD A COLORED BORDER ON BUTTONS */
.gradio-container .styler.svelte-iyf88w {
    border: 1.5px solid #F7D9DA !important;
    border-radius: 6px !important;  /* Adjust this value as needed */
    overflow: hidden !important;  /* This ensures the content doesn't spill out of the rounded corners */
}
.gradio-container .styler.svelte-iyf88w,
button.sm.secondary.svelte-cmf5ev > div {
    border-radius: 8px !important;  /* Slightly smaller than the outer border radius */
    background-color: white !important;  /* Or whatever background color you prefer */
    margin: 0 !important;  /* Remove any margin that might be causing gaps */
}

/* TO ADD A COLORED BORDER ON CHAT BOX */
.gradio-container .bubble-wrap.svelte-1e1jlin {
    border: 1.5px solid #F7D9DA !important;
    border-radius: 8px !important;  /* Adjust this value as needed */
    /* overflow: hidden !important;  /* This ensures the content doesn't spill out of the rounded corners */ */
    overflow-y: auto !important;  /* Enable vertical scrolling */
    max-height: 500px; /* Set a maximum height for the chat container */
}
.gradio-container .bubble-wrap.svelte-1e1jlin > div {
    border-radius: 10px !important;  /* Slightly smaller than the outer border radius */
    background-color: white !important;  /* Or whatever background color you prefer */
    margin: 0 !important;  /* Remove any margin that might be causing gaps */
}
"""

# To avoid inconsistencies with dark mode
js = """
function setLightTheme() {
  const url = new URL(window.location);
  if (url.searchParams.get('__theme') !== 'light') {
    url.searchParams.set('__theme', 'light');
    window.location.href = url.href;
  }
}
"""

# To add the CélineGPT logo in the Gradio interface
description_html = """
<div class="logo-container">
    <img src="https://huggingface.co/krogoldAI/CelineGPT-12B-240831/resolve/main/Pictures/C%C3%A9lineGPT.png" alt="Logo" class="logo">
</div>
"""

# Function generating model outputs
def stream(message, history):
    messages = [{"role": "system", "content": system_prompt}]
    for human, assistant in history:
        messages.append({"role": "user", "content": human})
        messages.append({"role": "assistant", "content": assistant})
    messages.append({"role": "user", "content": uniformisation(message)})

    prompt = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    inputs = tokenizer(prompt, return_tensors="pt").to(device)

    input_length = inputs["input_ids"].shape[1]
    generated_tokens = []

    with torch.no_grad():
        for i in range(1024):  # Adjust max_new_tokens as needed
            outputs = model.generate(
                **inputs,
                max_new_tokens=1,
                do_sample=True,
                temperature=0.7,
                pad_token_id=tokenizer.eos_token_id
            )
            
            new_token = outputs[0][input_length + i]
            if new_token == tokenizer.eos_token_id:
                break

            generated_tokens.append(new_token)
            
            # Decode all tokens together to preserve spacing
            streamed_text = tokenizer.decode(generated_tokens, skip_special_tokens=True)
            yield streamed_text

            # Update inputs for next iteration
            inputs = {"input_ids": outputs, "attention_mask": torch.ones_like(outputs)}

# Update the Gradio interface
demo = gr.ChatInterface(
    stream,
    title=None,
    description=description_html,
    textbox=gr.Textbox(placeholder="Posez n’importe quelle question !", container=False, scale=7),
    theme=custom_theme,
    cache_examples=True,
    retry_btn="Regénérer",
    undo_btn="Supprimer le dernier message",
    clear_btn="Réinitialiser la conversation",
    submit_btn="Envoyer",
    css=custom_css,
    js=js
)

demo.queue()

### Now, let's play with the model!

To launch the model with the Gradio interface, just execute:

In [ ]:
demo.launch()

If ```demo.launch()``` doesn't work, try this instead:

In [ ]:
demo.launch(server_name="0.0.0.0", share=True)

If this still doesn't work, try:

In [ ]:
import os

# Try to get the port from an environment variable, or use a default range
port = int(os.environ.get("GRADIO_SERVER_PORT", 0))

# Try ports 7860 to 7869 :
for port in range(7860, 7870):
    try:
        demo.launch(server_name="0.0.0.0", server_port=port, share=True)
        print(f"Gradio app is running on port {port}")
        break
    except OSError:
        continue
else:
    print("Could not find an available port")